In [3]:
import numpy as np
import skvideo.io
from base64 import b64encode
from IPython.display import HTML
from myosuite.utils.quat_math import quat2euler
from myosuite.utils import gym
import myosuite
from stable_baselines3 import PPO
import torch

def show_video(video_path, video_width=500):
    video_file = open(video_path, "r+b").read()
    video_url = f"data:video/mp4;base64,{b64encode(video_file).decode()}"
    return HTML(f"""<video autoplay width={video_width} controls><source src="{video_url}"></video>""")

# Load the environment
env = gym.make('myoLegWalk-v0', reset_type='random')

# Load the trained model (specify the correct path to your model file)
model = PPO.load("ppo_custom_leg_model.zip")

# Set higher resolution for the offscreen renderer
unwrapped_env = env.envs[0].unwrapped if hasattr(env, 'envs') else env.unwrapped
unwrapped_env.sim.model.vis.global_.offwidth = 1920
unwrapped_env.sim.model.vis.global_.offheight = 1080

# Evaluate the trained model
obs = env.reset()[0]  # Use only the observation part of the tuple
frames = []  # Initialize frames list

for _ in range(1000):
    action, _states = model.predict(obs)
    result = env.step(action)
    if len(result) == 5:
        obs, rewards, dones, info, _ = result  # Unpack the five values
    else:
        obs, rewards, dones, info = result  # Unpack the four values
    obs = obs[0] if isinstance(obs, tuple) else obs  # Ensure obs has the correct shape
    frame = unwrapped_env.sim.renderer.render_offscreen(camera_id=1)  # Access sim from unwrapped environment
    frames.append(frame)

# Save the frames as a video with higher resolution settings
skvideo.io.vwrite("walk_train2.mp4", 
                  np.asarray(frames), inputdict={"-r":"100"}, outputdict={"-r": "100", "-pix_fmt": "yuv420p", "-s": "1920x1080"})

# Show the video in the notebook
show_video("walk_train2.mp4")